In order to determine if there are neighborhoods in Manhattan nearer to the Financial District that are similar to Clinton Hill in Brooklyn we will begin by clustering Foursquare explore data for all the neighborhoods in both boroughs using k-means clustering. The first step is to download the necessary libraries to work with the data.

In [4]:
import numpy as np
import pandas as pd
pd.set_option('display.max_columns',None)
pd.set_option('display.max.rows',None)

import json

import requests
from pandas.io.json import json_normalize
import matplotlib.cm as cm
import matplotlib.colors as colors

from sklearn.cluster import KMeans

print ('Libraries imported.')

Libraries imported.


And, the mapping function libraries.

In [7]:
!conda install -c conda-forge geopy --yes
from geopy.geocoders import Nominatim

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    ca-certificates-2020.4.5.1 |       hecc5488_0         146 KB  conda-forge
    certifi-2020.4.5.1         |   py36h9f0ad1d_0         151 KB  conda-forge
    python_abi-3.6             |          1_cp36m           4 KB  conda-forge
    geographiclib-1.50         |             py_0          34 KB  conda-forge
    geopy-1.22.0               |     pyh9f0ad1d_0          63 KB  conda-forge
    openssl-1.1.1g             |       h516909a_0         2.1 MB  conda-forge
    ------------------------------------------------------------
                                           Total:         2.5 MB

The following NEW packages will be INSTALLED:

    geographiclib:   1.50-py_0           conda-forge
    geopy:          

In [2]:
get_ipython().system('pip install folium==0.5.0')
import folium

     |████████████████████████████████| 81kB 10.0MB/s eta 0:00:01
  Stored in directory: /home/dsxuser/.cache/pip/wheels/f8/98/ff/954791afc47740d554f0d9e5885fa09dd60c2265d42578e665
Successfully built folium


The next step is to bring in the geojson data for New York city neighborhoods.

In [6]:
!wget -q -O 'newyork_data.json' https://cocl.us/new_york_dataset
print('Data downloaded!')

Data downloaded!


In [7]:

import types
import pandas as pd
from botocore.client import Config
import ibm_boto3

with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)



In [10]:
newyork_data

{'type': 'FeatureCollection',
 'totalFeatures': 306,
 'features': [{'type': 'Feature',
   'id': 'nyu_2451_34572.1',
   'geometry': {'type': 'Point',
    'coordinates': [-73.84720052054902, 40.89470517661]},
   'geometry_name': 'geom',
   'properties': {'name': 'Wakefield',
    'stacked': 1,
    'annoline1': 'Wakefield',
    'annoline2': None,
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.84720052054902,
     40.89470517661,
     -73.84720052054902,
     40.89470517661]}},
  {'type': 'Feature',
   'id': 'nyu_2451_34572.2',
   'geometry': {'type': 'Point',
    'coordinates': [-73.82993910812398, 40.87429419303012]},
   'geometry_name': 'geom',
   'properties': {'name': 'Co-op City',
    'stacked': 2,
    'annoline1': 'Co-op',
    'annoline2': 'City',
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.82993910812398,
     40.87429419303012,
     -73.82993910812398,
     40.87429419303012]}},
  {'type': 'Feature',
 

In [8]:
neighborhoods_data =newyork_data['features']
neighborhoods_data[0]
                               

{'type': 'Feature',
 'id': 'nyu_2451_34572.1',
 'geometry': {'type': 'Point',
  'coordinates': [-73.84720052054902, 40.89470517661]},
 'geometry_name': 'geom',
 'properties': {'name': 'Wakefield',
  'stacked': 1,
  'annoline1': 'Wakefield',
  'annoline2': None,
  'annoline3': None,
  'annoangle': 0.0,
  'borough': 'Bronx',
  'bbox': [-73.84720052054902,
   40.89470517661,
   -73.84720052054902,
   40.89470517661]}}

In [9]:
column_names = ['Neighborhood','Latitude','Longitude']
neighborhoods_data = pd.DataFrame(columns=column_names)
neighborhoods_data

Empty DataFrame
Columns: [Neighborhood, Latitude, Longitude]
Index: []

Now we insert the location data into a dataframe called neighborhoods.

In [10]:

import types
import pandas as pd
from botocore.client import Config
import ibm_boto3

def __iter__(self): return 0

# @hidden_cell
# The following code accesses a file in your IBM Cloud Object Storage. It includes your credentials.
# You might want to remove those credentials before you share the notebook.
client_77c71a8d289e4e20ac6fa5cff69e0829 = ibm_boto3.client(service_name='s3',
    ibm_api_key_id='t9E0P0YkeGFbDTK9C2wiIGprVlk4qekIn3E83lGc0U0R',
    ibm_auth_endpoint="https://iam.cloud.ibm.com/oidc/token",
    config=Config(signature_version='oauth'),
    endpoint_url='https://s3-api.us-geo.objectstorage.service.networklayer.com')

body = client_77c71a8d289e4e20ac6fa5cff69e0829.get_object(Bucket='movingdatafornewyorkneighborhoods-donotdelete-pr-potmhbafafjdla',Key='geojsondatafornycn.csv')['Body']
# add missing __iter__ method, so pandas accepts body as file-like object
if not hasattr(body, "__iter__"): body.__iter__ = types.MethodType( __iter__, body )

neighborhoods = pd.read_csv(body)
neighborhoods.head()


Neighborhood   Latitude  Longitude
0    Bay Ridge  40.625801 -74.030621
1  Bensonhurst  40.611009 -73.995180
2  Sunset Park  40.645103 -74.010316
3   Greenpoint  40.730201 -73.954241
4    Gravesend  40.595260 -73.973471

We use the folium mapping library function in the next step to create a map of New York with the Brooklyn and Manhattan neighborhoods superimposed on top.

In [14]:
neighborhoods.shape[0]

110

In [15]:
map_newyork = folium.Map(location=[40.7127281,-74.0060152], zoom_start=10.5)

for lat,lng,neighborhood in zip(neighborhoods['Latitude'],neighborhoods['Longitude'],neighborhoods['Neighborhood']):
    label = '{}'.format(neighborhood)
    label = folium.Popup(label,parse_html=True)
    folium.CircleMarker(
        [lat,lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)

map_newyork

The next step is to bring in data about the neighborhoods from the Foursquare API to explore the neighborhoods and segment them. We start by loading the parameters for the exploration and creating the GET request URL.

In [13]:
CLIENT_ID = '1GF2ZURUPIUCMKFFK2JWUB34Z1CSFXO2GFTJ2BIGJMQIJRE2'
CLIENT_SECRET = '044X1QMU5HZGZCF1LHDCJCLL5ZY0VH1GL5HUYSIBMKQZSW55'
VERSION = '20200601'
print('Client Id: ' + CLIENT_ID)
print('Client Secret: '+ CLIENT_SECRET)

Client Id: 1GF2ZURUPIUCMKFFK2JWUB34Z1CSFXO2GFTJ2BIGJMQIJRE2
Client Secret: 044X1QMU5HZGZCF1LHDCJCLL5ZY0VH1GL5HUYSIBMKQZSW55


To begin, let's look at the first neighborhood on the list.

In [14]:
neighborhoods.loc[0,'Neighborhood']

'Bay Ridge'

In [15]:
neighborhood_latitude=neighborhoods.loc[0,'Latitude']
neighborhood_longitude=neighborhoods.loc[0,'Longitude']
neighborhood_name=neighborhoods.loc[0,'Neighborhood']
print(neighborhood_name ,neighborhood_latitude ,neighborhood_longitude)

Bay Ridge 40.62580107 -74.03062069


In [16]:
LIMIT=100
radius=500
url='https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID,
    CLIENT_SECRET,
    VERSION,
    neighborhood_latitude,
    neighborhood_longitude,
    radius,
    LIMIT)

url

'https://api.foursquare.com/v2/venues/explore?&client_id=1GF2ZURUPIUCMKFFK2JWUB34Z1CSFXO2GFTJ2BIGJMQIJRE2&client_secret=044X1QMU5HZGZCF1LHDCJCLL5ZY0VH1GL5HUYSIBMKQZSW55&v=20200601&ll=40.62580107,-74.03062069&radius=500&limit=100'

In [17]:
def get_category_type(row):
    try:
        categories_list=row['categories']
    except:
        categories_list=row['venue.categories']
    if len(categories_list)  == 0:
        return None
    else:
        return categories_list[0]['name']

In [18]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5ed6cf1ce826ac001b1212f0'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': '$-$$$$', 'key': 'price'},
    {'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'Bay Ridge',
  'headerFullLocation': 'Bay Ridge, Brooklyn',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 83,
  'suggestedBounds': {'ne': {'lat': 40.630301074500004,
    'lng': -74.02470273002741},
   'sw': {'lat': 40.6213010655, 'lng': -74.0365386499726}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4b895827f964a5206c2d32e3',
       'name': 'Pilo Arts Day Spa and Salon',
       'location': {'address': '8412 3rd Ave',
        'lat': 40.62474788273414,
        'lng': -74.03059056940135,
        'labeledLatLngs'

Here is the first five entries from Foursquare displayed in a dataframe.

In [19]:
venues =results['response']['groups'][0]['items']
nearby_venues = json_normalize(venues)
filtered_columns=['venue.name','venue.categories','venue.location.lat','venue.location.lng']
nearby_venues=nearby_venues.loc[:,filtered_columns]
nearby_venues['venue.categories']=nearby_venues.apply(get_category_type,axis=1)
nearby_venues.columns=[col.split(".")[-1] for col in nearby_venues.columns]
nearby_venues.head()

name      categories        lat        lng
0  Pilo Arts Day Spa and Salon             Spa  40.624748 -74.030591
1                    Bagel Boy      Bagel Shop  40.627896 -74.029335
2          Leo's Casa Calamari     Pizza Place  40.624200 -74.030931
3                 Pegasus Cafe  Breakfast Spot  40.623168 -74.031186
4          The Bookmark Shoppe       Bookstore  40.624577 -74.030562

In order to request data for all of the neighborhoods in our area of interest, we create a function that will iteratively generate data about up to 100 venues per neighborhood. This will be the basis of our analysis to categorize the neighborhoods as similar in terms of the types of venues in the neighborhood.

def getNearbyVenues(names,latitudes,longitudes,radius=500):
    
    venues_list=[]
    for name,lat,lng in zip(names,latitudes,longitudes):
        print(name)
        
        url1='https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID,
            CLIENT_SECRET,
            VERSION,
            lat,
            lng,
            radius,
            LIMIT)
        
        results=requests.get(url1).json()["response"]['groups'][0]['items']

        venues_list.append([(
            name,
            lat,
            lng,
            v['venue']['name'],
            v['venue']['location']['lat'],
            v['venue']['location']['lng'],
            v['venue']['categories'][0]['name'])for v in results])
    
    nearby_venues=pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns=['Neighborhood',
                    'Neighborhood Latitude',
                    'Neighborhood Longitude',
                    'Venue',
                    'Venue Latitude',
                    'Venue Longitude',
                    'Venue Category']
    return(nearby_venues)
    
    

The next piece of code will give us all the neighborhoods to be examined.

In [21]:
neighborhood_venues=getNearbyVenues(names=neighborhoods['Neighborhood'],
                                    latitudes=neighborhoods['Latitude'],
                                    longitudes=neighborhoods['Longitude']
                                   )
                                                       

Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker Heights
Gerritsen Beach
Marine Park
Clinton Hill
Sea Gate
Downtown
Boerum Hill
Prospect Lefferts Gardens
Ocean Hill
City Line
Bergen Beach
Midwood
Prospect Park South
Georgetown
East Williamsburg
North Side
South Side
Ocean Parkway
Fort Hamilton
Ditmas Park
Wingate
Rugby
Remsen Village
New Lots
Paerdegat Basin
Mill Basin
Fulton Ferry
Vinegar Hill
Weeksville
Broadway Junction
Dumbo
Homecrest
Highland Park
Madison
Erasmus
Marble Hill
Chinatown
Washington Heights
Inwood
Hamilton Heights
Manhattanville
Central Harlem
East Harlem
Upper East Side

And, here is the complete data frame of up to 100 venues per neighborhood in Brooklyn and Manhattan.

In [22]:
print(neighborhood_venues.shape)
neighborhood_venues

(5837, 7)


Neighborhood  Neighborhood Latitude  \
0                     Bay Ridge              40.625801   
1                     Bay Ridge              40.625801   
2                     Bay Ridge              40.625801   
3                     Bay Ridge              40.625801   
4                     Bay Ridge              40.625801   
5                     Bay Ridge              40.625801   
6                     Bay Ridge              40.625801   
7                     Bay Ridge              40.625801   
8                     Bay Ridge              40.625801   
9                     Bay Ridge              40.625801   
10                    Bay Ridge              40.625801   
11                    Bay Ridge              40.625801   
12                    Bay Ridge              40.625801   
13                    Bay Ridge              40.625801   
14                    Bay Ridge              40.625801   
15                    Bay Ridge              40.625801   
16                    Bay Ridge              40.625801   
17                    Bay Ridge              40.625801   
18                    Bay Ridge              40.625801   
19                    Bay Ridge              40.625801   
20                    Bay Ridge              40.625801   
21                    Bay Ridge              40.625801   
22                    Bay Ridge              40.625801   
23                    Bay Ridge              40.625801   
24                    Bay Ridge              40.625801   
25                    Bay Ridge              40.625801   
26                    Bay Ridge              40.625801   
27                    Bay Ridge              40.625801   
28                    Bay Ridge              40.625801   
29                    Bay Ridge              40.625801   
30                    Bay Ridge              40.625801   
31                    Bay Ridge              40.625801   
32                    Bay Ridge              40.625801   
33                    Bay Ridge              40.625801   
34                    Bay Ridge              40.625801   
35                    Bay Ridge              40.625801   
36                    Bay Ridge              40.625801   
37                    Bay Ridge              40.625801   
38                    Bay Ridge              40.625801   
39                    Bay Ridge              40.625801   
40                    Bay Ridge              40.625801   
41                    Bay Ridge              40.625801   
42                    Bay Ridge              40.625801   
43                    Bay Ridge              40.625801   
44                    Bay Ridge              40.625801   
45                    Bay Ridge              40.625801   
46                    Bay Ridge              40.625801   
47                    Bay Ridge              40.625801   
48                    Bay Ridge              40.625801   
49                    Bay Ridge              40.625801   
50                    Bay Ridge              40.625801   
51                    Bay Ridge              40.625801   
52                    Bay Ridge              40.625801   
53                    Bay Ridge              40.625801   
54                    Bay Ridge              40.625801   
55                    Bay Ridge              40.625801   
56                    Bay Ridge              40.625801   
57                    Bay Ridge              40.625801   
58                    Bay Ridge              40.625801   
59                    Bay Ridge              40.625801   
60                    Bay Ridge              40.625801   
61                    Bay Ridge              40.625801   
62                    Bay Ridge              40.625801   
63                    Bay Ridge              40.625801   
64                    Bay Ridge              40.625801   
65                    Bay Ridge              40.625801   
66                    Bay Ridge              40.625801   
67                    Bay Ridge              40.625801   
68               

In [23]:
print('There are {} unique categories of venues in the data frame.'.format(len(neighborhood_venues['Venue Category'].unique())))

There are 386 unique categories of venues in the data frame.


The next step is to analyse each neighborhood in preparation for clustering.

In [24]:
venues_onehot=pd.get_dummies(neighborhood_venues[['Venue Category']],prefix="",prefix_sep="")
venues_onehot['Neighborhood']=neighborhood_venues['Neighborhood']
fixed_columns=[venues_onehot.columns[-1]] + list(venues_onehot.columns[:-1])
venues_onehot = venues_onehot[fixed_columns]
venues_onehot.head()

Yoga Studio  Accessories Store  Adult Boutique  Afghan Restaurant  \
0            0                  0               0                  0   
1            0                  0               0                  0   
2            0                  0               0                  0   
3            0                  0               0                  0   
4            0                  0               0                  0   

   African Restaurant  Airport Terminal  American Restaurant  Animal Shelter  \
0                   0                 0                    0               0   
1                   0                 0                    0               0   
2                   0                 0                    0               0   
3                   0                 0                    0               0   
4                   0                 0                    0               0   

   Antique Shop  Arcade  Arepa Restaurant  Argentinian Restaurant  \
0             0       0                 0                       0   
1             0       0                 0                       0   
2             0       0                 0                       0   
3             0       0                 0                       0   
4             0       0                 0                       0   

   Art Gallery  Art Museum  Arts & Crafts Store  Arts & Entertainment  \
0            0           0                    0                     0   
1            0           0                    0                     0   
2            0           0                    0                     0   
3            0           0                    0                     0   
4            0           0                    0                     0   

   Asian Restaurant  Athletics & Sports  Auditorium  Australian Restaurant  \
0                 0                   0           0                      0   
1                 0                   0           0                      0   
2                 0                   0           0                      0   
3                 0                   0           0                      0   
4                 0                   0           0                      0   

   Austrian Restaurant  Auto Garage  BBQ Joint  Baby Store  Bagel Shop  \
0                    0            0          0           0           0   
1                    0            0          0           0           1   
2                    0            0          0           0           0   
3                    0            0          0           0           0   
4                    0            0          0           0           0   

   Bakery  Bank  Bar  Baseball Field  Baseball Stadium  Basketball Court  \
0       0     0    0               0                 0                 0   
1       0     0    0               0                 0                 0   
2       0     0    0               0                 0                 0   
3       0     0    0               0                 0                 0   
4       0     0    0               0                 0                 0   

   Basketball Stadium  Beach  Beer Bar  Beer Garden  Beer Store  \
0                   0      0         0            0           0   
1                   0      0         0            0           0   
2                   0      0         0            0           0   
3                   0      0         0            0           0   
4                   0      0         0            0           0   

   Big Box Store  Bike Rental / Bike Share  Bike Shop  Bike Trail  Bistro  \
0              0                         0          0           0       0   
1              0                         0          0           0       0   
2              0                         0          0           0       0   
3              0                         0          0           0       0   
4              0                         0          0           0       0   

In [25]:
venues_onehot.shape

(5837, 386)

The next step is to group the types of venues by Neighborhood.

In [26]:
venues_grouped=venues_onehot.groupby('Neighborhood').mean().reset_index()
venues_grouped

Neighborhood  Yoga Studio  Accessories Store  \
0                   Bath Beach     0.000000           0.000000   
1            Battery Park City     0.000000           0.000000   
2                    Bay Ridge     0.000000           0.000000   
3           Bedford Stuyvesant     0.000000           0.000000   
4                  Bensonhurst     0.000000           0.000000   
5                 Bergen Beach     0.000000           0.000000   
6                  Boerum Hill     0.021739           0.000000   
7                 Borough Park     0.000000           0.000000   
8               Brighton Beach     0.000000           0.000000   
9            Broadway Junction     0.000000           0.000000   
10            Brooklyn Heights     0.040000           0.000000   
11                 Brownsville     0.000000           0.000000   
12                    Bushwick     0.000000           0.000000   
13                    Canarsie     0.000000           0.000000   
14               Carnegie Hill     0.036145           0.000000   
15             Carroll Gardens     0.000000           0.000000   
16              Central Harlem     0.000000           0.000000   
17                     Chelsea     0.000000           0.000000   
18                   Chinatown     0.010000           0.000000   
19                   City Line     0.000000           0.000000   
20                Civic Center     0.020619           0.000000   
21                     Clinton     0.000000           0.000000   
22                Clinton Hill     0.032609           0.000000   
23                 Cobble Hill     0.031915           0.000000   
24                Coney Island     0.000000           0.000000   
25               Crown Heights     0.000000           0.000000   
26               Cypress Hills     0.000000           0.000000   
27                 Ditmas Park     0.022727           0.000000   
28                    Downtown     0.010000           0.000000   
29                       Dumbo     0.033898           0.000000   
30               Dyker Heights     0.000000           0.000000   
31               East Flatbush     0.000000           0.000000   
32                 East Harlem     0.000000           0.000000   
33               East New York     0.000000           0.000000   
34                East Village     0.000000           0.000000   
35           East Williamsburg     0.000000           0.000000   
36                     Erasmus     0.043478           0.000000   
37          Financial District     0.010000           0.000000   
38                    Flatbush     0.000000           0.000000   
39                    Flatiron     0.030000           0.000000   
40                   Flatlands     0.000000           0.000000   
41                 Fort Greene     0.014925           0.000000   
42               Fort Hamilton     0.000000           0.000000   
43                Fulton Ferry     0.000000           0.000000   
44                  Georgetown     0.000000           0.000000   
45             Gerritsen Beach     0.000000           0.000000   
46                     Gowanus     0.028986           0.000000   
47                    Gramercy     0.011628           0.000000   
48                   Gravesend     0.000000           0.000000   
49                  Greenpoint     0.030000           0.000000   
50           Greenwich Village     0.010000           0.000000   
51            Hamilton Heights     0.033898           0.000000   
52               Highland Park     0.000000           0.000000   
53                   Homecrest     0.000000           0.000000   
54                Hudson Yards     0.000000           0.000000   
55                      Inwood     0.017544           0.000000   
56                  Kensington     0.000000           0.000000   
57                  Lenox Hill     0.010000           0.000000   
58              Lincoln Square     0.010309           0.000000   
59                Little Italy     0.000000           0.00

Now we print a list of each neighborhood with the top 10 most common venues in the neighborhood.

In [27]:
num_top_venues=10

for hood in venues_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp=venues_grouped[venues_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns=['venue','freq']
    temp=temp.iloc[1:]
    temp['freq']=temp['freq'].astype(float)
    temp=temp.round({'freq':2})
    print(temp.sort_values('freq',ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Bath Beach----
                  venue  freq
0              Pharmacy  0.07
1    Chinese Restaurant  0.07
2           Gas Station  0.04
3       Bubble Tea Shop  0.04
4  Fast Food Restaurant  0.04
5    Italian Restaurant  0.04
6  Cantonese Restaurant  0.04
7           Pizza Place  0.04
8                Bakery  0.02
9                  Bank  0.02


----Battery Park City----
           venue  freq
0           Park  0.12
1          Hotel  0.06
2    Coffee Shop  0.06
3  Memorial Site  0.05
4            Gym  0.05
5    Beer Garden  0.03
6          Plaza  0.03
7  Boat or Ferry  0.03
8     Playground  0.03
9   Gourmet Shop  0.03


----Bay Ridge----
                 venue  freq
0   Italian Restaurant  0.07
1                  Spa  0.07
2          Pizza Place  0.05
3   Chinese Restaurant  0.05
4                  Bar  0.04
5     Greek Restaurant  0.04
6           Bagel Shop  0.04
7  American Restaurant  0.04
8       Ice Cream Shop  0.02
9      Thai Restaurant  0.02


----Bedford Stuyvesant----
  

                venue  freq
0         Pizza Place  0.16
1              Museum  0.11
2                Café  0.11
3        Burger Joint  0.05
4              Bakery  0.05
5          Bagel Shop  0.05
6         Candy Store  0.05
7         Coffee Shop  0.05
8            Pharmacy  0.05
9  Salon / Barbershop  0.05


----Cypress Hills----
                       venue  freq
0        Fried Chicken Joint  0.12
1         Spanish Restaurant  0.08
2                Pizza Place  0.08
3             Ice Cream Shop  0.08
4       Fast Food Restaurant  0.08
5                 Donut Shop  0.08
6               Dance Studio  0.04
7  Latin American Restaurant  0.04
8         Seafood Restaurant  0.04
9                       Bank  0.04


----Ditmas Park----
                  venue  freq
0         Deli / Bodega  0.09
1            Donut Shop  0.05
2  Caribbean Restaurant  0.05
3    Chinese Restaurant  0.05
4          Liquor Store  0.05
5        Discount Store  0.05
6           Pizza Place  0.05
7              Pharma

                venue  freq
0                 Bar  0.10
1         Pizza Place  0.08
2        Cocktail Bar  0.06
3         Coffee Shop  0.06
4  Mexican Restaurant  0.03
5    Sushi Restaurant  0.03
6                Café  0.03
7         Yoga Studio  0.03
8   French Restaurant  0.03
9              Bakery  0.02


----Greenwich Village----
                 venue  freq
0   Italian Restaurant  0.08
1                 Café  0.05
2     Sushi Restaurant  0.04
3                  Gym  0.03
4          Pizza Place  0.03
5  Indie Movie Theater  0.02
6               Bakery  0.02
7                  Bar  0.02
8    Indian Restaurant  0.02
9       Ice Cream Shop  0.02


----Hamilton Heights----
                venue  freq
0         Pizza Place  0.08
1         Coffee Shop  0.07
2       Deli / Bodega  0.07
3                Café  0.05
4  Mexican Restaurant  0.05
5         Yoga Studio  0.03
6   Indian Restaurant  0.03
7      Sandwich Place  0.03
8              School  0.03
9        Cocktail Bar  0.03


----High

                      venue  freq
0                     Hotel  0.05
1            Sandwich Place  0.05
2               Pizza Place  0.04
3               Coffee Shop  0.04
4      Gym / Fitness Center  0.04
5              Burger Joint  0.03
6  Mediterranean Restaurant  0.03
7          Cuban Restaurant  0.03
8                      Café  0.03
9       Japanese Restaurant  0.03


----New Lots----
                 venue  freq
0   Chinese Restaurant  0.10
1  Fried Chicken Joint  0.10
2        Grocery Store  0.10
3             Pharmacy  0.10
4           Playground  0.05
5                 Park  0.05
6                 Bank  0.05
7   Salon / Barbershop  0.05
8       Breakfast Spot  0.05
9          Pizza Place  0.05


----Noho----
                 venue  freq
0          Pizza Place  0.06
1          Coffee Shop  0.06
2   Italian Restaurant  0.05
3        Grocery Store  0.04
4       Sandwich Place  0.04
5  Japanese Restaurant  0.04
6            Wine Shop  0.03
7   Mexican Restaurant  0.03
8           

                 venue  freq
0   Italian Restaurant  0.06
1                 Park  0.06
2  American Restaurant  0.05
3             Wine Bar  0.04
4               Bakery  0.04
5                 Café  0.04
6                  Spa  0.04
7          Coffee Shop  0.04
8           Skate Park  0.03
9     Greek Restaurant  0.03


----Tudor City----
                  venue  freq
0                  Café  0.07
1                  Park  0.07
2    Mexican Restaurant  0.05
3         Deli / Bodega  0.04
4      Sushi Restaurant  0.04
5                   Bar  0.03
6  Gym / Fitness Center  0.03
7       Thai Restaurant  0.03
8      Greek Restaurant  0.03
9                   Gym  0.03


----Turtle Bay----
                venue  freq
0    Sushi Restaurant  0.04
1         Coffee Shop  0.04
2            Wine Bar  0.04
3                Café  0.04
4                Park  0.04
5  Italian Restaurant  0.04
6   French Restaurant  0.03
7  Seafood Restaurant  0.03
8       Deli / Bodega  0.03
9             Dog Run  0.02



Now we create a dataframe with this information.

In [28]:
def return_most_common_venues(row,num_top_venues):
    row_categories =row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [29]:
num_top_venues=10
indicators=['st','nd','rd']
columns=['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1,indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

neighborhood_venues_sorted=pd.DataFrame(columns=columns)
neighborhood_venues_sorted['Neighborhood']=venues_grouped['Neighborhood']

for ind in np.arange(venues_grouped.shape[0]):
    neighborhood_venues_sorted.iloc[ind,1:]=return_most_common_venues(venues_grouped.iloc[ind,:], num_top_venues)
    
neighborhood_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0          Bath Beach              Pharmacy    Chinese Restaurant   
1   Battery Park City                  Park           Coffee Shop   
2           Bay Ridge                   Spa    Italian Restaurant   
3  Bedford Stuyvesant                   Bar           Coffee Shop   
4         Bensonhurst           Pizza Place          Dessert Shop   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0  Fast Food Restaurant    Italian Restaurant           Pizza Place   
1                 Hotel                   Gym         Memorial Site   
2    Chinese Restaurant           Pizza Place                   Bar   
3           Pizza Place                  Café            Bagel Shop   
4      Sushi Restaurant    Italian Restaurant            Donut Shop   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0       Bubble Tea Shop  Cantonese Restaurant           Gas Station   
1           Beer Garden         Shopping Mall          Gourmet Shop   
2            Bagel Shop   American Restaurant      Greek Restaurant   
3              Boutique             Gift Shop          Gourmet Shop   
4                Bakery        Ice Cream Shop                  Park   

  9th Most Common Venue  10th Most Common Venue  
0   Rental Car Location             Coffee Shop  
1            Food Court                   Plaza  
2            Playground           Grocery Store  
3             BBQ Joint  Thrift / Vintage Store  
4             Pet Store      Russian Restaurant

We will segment into 12 clusters, each cluster made up of neighborhoods with the similar common venue types.

In [30]:
from sklearn.cluster import KMeans
kclusters=12
venues_grouped_clustering=venues_grouped.drop('Neighborhood',1)
kmeans=KMeans(n_clusters=kclusters,random_state=0).fit(venues_grouped_clustering)
kmeans.labels_[0:12]

array([10,  0,  4,  9,  4,  5,  4, 10, 10, 10,  0,  0], dtype=int32)

And add the cluster information to the data frame.

In [31]:
neighborhood_venues_sorted.insert(0,'Cluster',kmeans.labels_)
venues_merged=neighborhoods
venues_merged=venues_merged.join(neighborhood_venues_sorted.set_index('Neighborhood'),on='Neighborhood')
venues_merged.head()

Neighborhood   Latitude  Longitude  Cluster 1st Most Common Venue  \
0    Bay Ridge  40.625801 -74.030621        4                   Spa   
1  Bensonhurst  40.611009 -73.995180        4           Pizza Place   
2  Sunset Park  40.645103 -74.010316       10           Pizza Place   
3   Greenpoint  40.730201 -73.954241        9                   Bar   
4    Gravesend  40.595260 -73.973471       10                Lounge   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0    Italian Restaurant    Chinese Restaurant           Pizza Place   
1          Dessert Shop      Sushi Restaurant    Italian Restaurant   
2    Mexican Restaurant                  Bank                Bakery   
3           Pizza Place           Coffee Shop          Cocktail Bar   
4           Pizza Place                Bakery   Sporting Goods Shop   

       5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0                        Bar            Bagel Shop   American Restaurant   
1                 Donut Shop                Bakery        Ice Cream Shop   
2  Latin American Restaurant     Mobile Phone Shop                   Gym   
3                Yoga Studio     French Restaurant    Mexican Restaurant   
4             Farmers Market    Chinese Restaurant                   Bar   

  8th Most Common Venue 9th Most Common Venue  10th Most Common Venue  
0      Greek Restaurant            Playground           Grocery Store  
1                  Park             Pet Store      Russian Restaurant  
2              Pharmacy   Fried Chicken Joint             Record Shop  
3      Sushi Restaurant                  Café  Thrift / Vintage Store  
4                   Gym            Donut Shop  Furniture / Home Store

Folium allows us to visualize the clusters. In this way we can see if any neighborhoods in the same category (cluster) as Clinton Hill are closer to the target neighborhood, the Financial District, where our client's office is.

In [39]:
map_clusters=folium.Map(location=[40.7127281,-74.0060152], zoom_start=10.5)
x=np.arange(kclusters)
ys=[i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0,1,len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]
markers_colors = []
for lat,lon,poi,cluster in zip(venues_merged['Latitude'],venues_merged['Longitude'],venues_merged['Neighborhood'],venues_merged['Cluster']):
    label = folium.Popup(str(poi) + ', Cluster ' + str(cluster),parse_html=True)
    folium.CircleMarker(
    [lat,lon],
    radius=5,
    popup=label,
    color=rainbow[cluster-1],
    fill=True,
    fill_color=rainbow[cluster-1],
    fill_opacity=0.7).add_to(map_clusters)
    
map_clusters

Let's reorganize the data frame by cluster to see what neighborhoods are similar to Clinton Hill and what types of venues this cluster offers.

In [32]:
neighborhood_clusters=venues_merged.sort_values(['Cluster'],ascending=True)
neighborhood_clusters

Neighborhood   Latitude  Longitude  Cluster  \
54                 Ditmas Park  40.643675 -73.961013        0   
81            Roosevelt Island  40.762160 -73.949168        0   
26               East New York  40.669926 -73.880699        0   
32                Coney Island  40.574293 -73.988683        0   
55                     Wingate  40.660947 -73.937187        0   
77                 East Harlem  40.792249 -73.944182        0   
73                      Inwood  40.867684 -73.921210        0   
37                 Marine Park  40.609748 -73.931344        0   
18            Brooklyn Heights  40.695864 -73.993782        0   
72          Washington Heights  40.851903 -73.936900        0   
96         Morningside Heights  40.808000 -73.963896        0   
12             Windsor Terrace  40.656946 -73.980073        0   
14                 Brownsville  40.663950 -73.910235        0   
10               East Flatbush  40.641718 -73.936103        0   
106                 Tudor City  40.746917 -73.971219        0   
58                    New Lots  40.662744 -73.885118        0   
61                Fulton Ferry  40.703281 -73.995508        0   
98           Battery Park City  40.711932 -74.016869        0   
67               Highland Park  40.681999 -73.890346        0   
42   Prospect Lefferts Gardens  40.658420 -73.954899        0   
43                  Ocean Hill  40.678403 -73.913068        0   
11                  Kensington  40.642382 -73.980421        0   
63                  Weeksville  40.675040 -73.930531        0   
30                 Mill Island  40.606336 -73.908186        1   
39                    Sea Gate  40.576375 -74.007873        2   
28                    Canarsie  40.635564 -73.902093        3   
78             Upper East Side  40.775639 -73.960508        4   
71                   Chinatown  40.715618 -73.994279        4   
80                  Lenox Hill  40.768113 -73.958860        4   
65                       Dumbo  40.703176 -73.988753        4   
85                     Midtown  40.754691 -73.981669        4   
83              Lincoln Square  40.773529 -73.985338        4   
105                 Turtle Bay  40.752042 -73.967708        4   
104               Sutton Place  40.760280 -73.963556        4   
103              Midtown South  40.748510 -73.988713        4   
102               Civic Center  40.715229 -74.005415        4   
101                       Noho  40.723259 -73.988434        4   
100              Carnegie Hill  40.782683 -73.953256        4   
99          Financial District  40.707107 -74.010665        4   
82             Upper West Side  40.787658 -73.977059        4   
94                West Village  40.734434 -74.006180        4   
92                Little Italy  40.719324 -73.997305        4   
91                     Tribeca  40.721522 -74.010683        4   
90             Lower East Side  40.717807 -73.980890        4   
88           Greenwich Village  40.726933 -73.999914        4   
87                     Chelsea  40.744035 -74.003116        4   
86                 Murray Hill  40.748303 -73.978332        4   
84                     Clinton  40.759101 -73.996119        4   
93                        Soho  40.722184 -74.000657        4   
108                   Flatiron  40.739673 -73.990947        4   
0                    Bay Ridge  40.625801 -74.030621        4   
109               Hudson Yards  40.756658 -74.000111        4   
40                    Downtown  40.690844 -73.983463        4   
41                 Boerum Hill  40.685683 -73.983748        4   
24                  Park Slope  40.672321 -73.977050        4   
23                 Fort Greene  40.688527 -73.972906        4   
1                  Bensonhurst  40.611009 -73.995180        4   
6               Sheepshead Bay  40.586890 -73.943186        4   
20             Carroll Gardens  40.680540 -73.994654        4   
107            Stuyvesant Town  40.731000 -73.974052        5   
45                Bergen Beach  40.615150 -73.898556 

And let's focus in on cluster 9 which is the cluster Clinton Hill falls into.

In [33]:
cluster9_df=neighborhood_clusters.loc[neighborhood_clusters['Cluster'] == 9]
cluster9_df

Neighborhood   Latitude  Longitude  Cluster 1st Most Common Venue  \
31     Manhattan Beach  40.577914 -73.943537        9              Bus Stop   
22             Gowanus  40.673931 -73.994441        9                   Bar   
21            Red Hook  40.676253 -74.012759        9           Art Gallery   
89        East Village  40.727847 -73.982226        9                   Bar   
16            Bushwick  40.698116 -73.925258        9         Deli / Bodega   
17  Bedford Stuyvesant  40.687232 -73.941785        9                   Bar   
15        Williamsburg  40.707144 -73.958115        9           Coffee Shop   
95    Manhattan Valley  40.797307 -73.964286        9           Coffee Shop   
13    Prospect Heights  40.676822 -73.964859        9                   Bar   
97            Gramercy  40.737210 -73.981376        9            Bagel Shop   
9        Crown Heights  40.670829 -73.943291        9           Pizza Place   
3           Greenpoint  40.730201 -73.954241        9                   Bar   
19         Cobble Hill  40.687920 -73.998561        9           Coffee Shop   
50          North Side  40.714823 -73.958809        9           Coffee Shop   
51          South Side  40.710861 -73.958001        9           Coffee Shop   
62        Vinegar Hill  40.703322 -73.981116        9            Food Truck   
76      Central Harlem  40.815976 -73.943211        9    African Restaurant   
75      Manhattanville  40.816934 -73.957385        9           Coffee Shop   
52       Ocean Parkway  40.613060 -73.968367        9           Pizza Place   
74    Hamilton Heights  40.823604 -73.949688        9           Pizza Place   
36     Gerritsen Beach  40.590848 -73.930102        9        Ice Cream Shop   
38        Clinton Hill  40.693229 -73.967843        9    Italian Restaurant   
79           Yorkville  40.775930 -73.947118        9           Coffee Shop   
49   East Williamsburg  40.708492 -73.938858        9                   Bar   
68             Madison  40.609378 -73.948415        9            Bagel Shop   

     2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
31                    Food        Ice Cream Shop        Sandwich Place   
22  Furniture / Home Store    Italian Restaurant           Pizza Place   
21      Seafood Restaurant                   Bar                  Park   
89      Mexican Restaurant          Cocktail Bar           Coffee Shop   
16                     Bar    Mexican Restaurant           Coffee Shop   
17             Coffee Shop           Pizza Place                  Café   
15              Bagel Shop                   Bar          Burger Joint   
95             Yoga Studio                   Bar           Pizza Place   
13      Mexican Restaurant             Wine Shop       Thai Restaurant   
97                     Bar           Coffee Shop           Pizza Place   
9                   Museum                  Café            Playground   
3              Pizza Place           Coffee Shop          Cocktail Bar   
19              Playground           Pizza Place                   Bar   
50             Pizza Place           Yoga Studio   American Restaurant   
51                     Bar           Pizza Place   American Restaurant   
62             Coffee Shop           Art Gallery                  Café   
76          Cosmetics Shop                   Bar    Seafood Restaurant   
75      Seafood Restaurant                  Park    Mexican Restaurant   
52        Sushi Restaurant            Playground           Men's Store   
74             Coffee Shop         Deli / Bodega                  Café   
36             Pizza Place                   Bar            Bagel Shop   
38             Pizza Place    Mexican Restaurant             Wine Shop   
79                     Gym    Italian Restaurant                   Bar   
49           Deli / Bodega                Bakery           Coffee Shop   
68          Pilates Studio            Restaurant          Dessert Shop   

   5th Most Common Venue      

The Financial District itself is in cluster 4 and our client has already told us that she believes it is not ideal a a place to live. So we want to narrow the search down to neighborhoods in cluster 9 that are closer to the Financial District than Clinton Hill.

In [39]:
nearer_neighborhood=cluster9_df[(cluster9_df['Neighborhood'] == 'Clinton Hill') | (cluster9_df['Neighborhood'] == 'Vinegar Hill') | (cluster9_df['Neighborhood'] == 'East Village') | (cluster9_df['Neighborhood'] == 'Gramercy') | (cluster9_df['Neighborhood'] == 'Cobble Hill')]
nearer_neighborhood

Neighborhood   Latitude  Longitude  Cluster 1st Most Common Venue  \
89  East Village  40.727847 -73.982226        9                   Bar   
97      Gramercy  40.737210 -73.981376        9            Bagel Shop   
19   Cobble Hill  40.687920 -73.998561        9           Coffee Shop   
62  Vinegar Hill  40.703322 -73.981116        9            Food Truck   
38  Clinton Hill  40.693229 -73.967843        9    Italian Restaurant   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
89    Mexican Restaurant          Cocktail Bar           Coffee Shop   
97                   Bar           Coffee Shop           Pizza Place   
19            Playground           Pizza Place                   Bar   
62           Coffee Shop           Art Gallery                  Café   
38           Pizza Place    Mexican Restaurant             Wine Shop   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
89           Pizza Place        Ice Cream Shop      Ramen Restaurant   
97         Grocery Store    Mexican Restaurant            Playground   
19           Yoga Studio    Italian Restaurant        Ice Cream Shop   
62             Wine Shop        Ice Cream Shop               Factory   
38       Thai Restaurant            Restaurant   Japanese Restaurant   

   8th Most Common Venue  9th Most Common Venue 10th Most Common Venue  
89             Juice Bar    Japanese Restaurant               Wine Bar  
97   American Restaurant     Italian Restaurant           Cocktail Bar  
19         Deli / Bodega           Cocktail Bar             Restaurant  
62                  Park  Performing Arts Venue              Bookstore  
38           Yoga Studio      Indian Restaurant                  Diner

And add the average rental price for the neighborhood. As there are only five neighborhoods that fit the cluster and location criteria we will simply add the column and data using insert.

In [41]:
nearer_neighborhood.insert(4,'Average Rental',['$3150','$3900','$3500','$3900','$2995'])
nearer_neighborhood

Neighborhood   Latitude  Longitude  Cluster Average Rental  \
89  East Village  40.727847 -73.982226        9          $3150   
97      Gramercy  40.737210 -73.981376        9          $3900   
19   Cobble Hill  40.687920 -73.998561        9          $3500   
62  Vinegar Hill  40.703322 -73.981116        9          $3900   
38  Clinton Hill  40.693229 -73.967843        9          $2995   

   1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
89                   Bar    Mexican Restaurant          Cocktail Bar   
97            Bagel Shop                   Bar           Coffee Shop   
19           Coffee Shop            Playground           Pizza Place   
62            Food Truck           Coffee Shop           Art Gallery   
38    Italian Restaurant           Pizza Place    Mexican Restaurant   

   4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
89           Coffee Shop           Pizza Place        Ice Cream Shop   
97           Pizza Place         Grocery Store    Mexican Restaurant   
19                   Bar           Yoga Studio    Italian Restaurant   
62                  Café             Wine Shop        Ice Cream Shop   
38             Wine Shop       Thai Restaurant            Restaurant   

   7th Most Common Venue 8th Most Common Venue  9th Most Common Venue  \
89      Ramen Restaurant             Juice Bar    Japanese Restaurant   
97            Playground   American Restaurant     Italian Restaurant   
19        Ice Cream Shop         Deli / Bodega           Cocktail Bar   
62               Factory                  Park  Performing Arts Venue   
38   Japanese Restaurant           Yoga Studio      Indian Restaurant   

   10th Most Common Venue  
89               Wine Bar  
97           Cocktail Bar  
19             Restaurant  
62              Bookstore  
38                  Diner

It appears that the East Village in Manhattan would be a good choice as a neighborhood with similar rental prices and venue types that is closer than Clinton Hill to the Financial District. 